# The Faust box API in DawDreamer

[![Open in Colab](https://colab.research.google.com/assets/colab-badge.svg)](http://colab.research.google.com/github/DBraun/DawDreamer/blob/main/examples/Box_API/Faust_Box_API.ipynb)

[DawDreamer](https://github.com/DBraun/DawDreamer/) provides Python bindings to the Faust box API, which is an intermediate representation of Faust. This creates many opportunities and even has some advantages over writing Faust code.
* Anything you can do with Faust code you can do with the box API thanks to the `boxFromDSP` function.
* Python scripting in the box API can lead to more optimized DSP code. For example, imagine Faust code with a "bypass" parameter for a reverb effect. Even if the bypass is enabled, the reverb effect is **always** computing. You are just mixing in 0% of it. With the box API, you can programatically connect/disconnect the reverb effect, allowing for faster DSP code!
* You can evaluate boxes in DawDreamer, pass audio to them, and automate their parameters over time. It even works for polyphonic instruments.
* You can export boxes to other languages such as C++ and JAX.
* * `boxToSource(box, "cpp", "MyDSP")`
* * `boxToSource(box, "jax", "MyDSP", ["-a", "jax/minimal.py"])`
* The relative simplicity of the box API makes it suitable for evolutionary algorithms and programmatic exploration of DSP blocks.

What follows is a Python-specific adaptation of [Faust's tutorial of the C++ box API](https://faustdoc.grame.fr/tutorials/box-api/).

## Using the box API

The box API grants access to an intermediate stage of the Faust compilation chain. In this tutorial, we present the API with Python bindings. The goal is to show how new audio DSP languages (textual or graphical) and algorithms could be built on top of the box API and benefit from the downstream Faust compiler infrastructure.

## Faust compiler structure

The Faust compiler is composed of several steps:
![compilation-chain.png](https://faustdoc.grame.fr/tutorials/box-api/img/compilation-chain.png)
<center><i>The compilation chain</i></center>

Starting from the DSP source code, the *Semantic Phase* produces signals as conceptually infinite streams of samples or control values. Those signals are then compiled in imperative code (C/C++, LLVM IR, WebAssembly, etc.) in the *Code Generation Phase*.

The *Semantic Phase* itself is composed of several steps:

![semantic-phase.png](https://faustdoc.grame.fr/tutorials/box-api/img/semantic-phase.png)
<center><i>The semantic phase</i></center>

The initial DSP code using the Block Diagram Algebra (BDA) is translated in a flat circuit in normal form in the *Evaluation, lambda-calculus* step.

The list of output signals is produced by the *Symbolic Propagation* step. Each output signal is then simplified and a set of optimizations are done (normal form computation and simplification, delay line sharing, typing, etc.) to finally produce a *list of output signals in normal form*.

The *Code Generation Phase* translates the signals to an intermediate representation named FIR (Faust Imperative Representation) which is then converted to the final target language (C/C++, LLVM IR, WebAssembly, Python JAX, etc.) with a set of backends.

## Accessing the box stage

A new intermediate public entry point has been created in the *Semantic Phase*, after the *Evaluation, lambda-calculus step* to allow the creation of a box expression. The box API enables programmatic creation of box expressions which can be translated to ready-to-use C++ classes, or LLVM, Interpreter or WebAssembly factories, to be used with all existing architecture files. Several optimizations done at the signal stage will be demonstrated by looking at the generated C++ code.

Note that the [signal API](https://dirt.design/DawDreamer/_generate/dawdreamer.faust.signal.html) allows to access another stage in the compilation process.

## Compiling box expressions

To use the box API, the following steps must be taken:

* Create a global compilation context using the `createLibContext` function.

* Create box expressions using the box API, progressively building more complex expressions by combining simpler ones.

* Compile any of the box expressions with a DawDreamer [FaustProcessor](https://dirt.design/DawDreamer/_generate/dawdreamer.FaustProcessor.html) `faust_processor.compile_box` (or compile to source code in a target language `boxToSource`).

* Finally, destroy the compilation context using the `destroyLibContext` function.

As an alternative to book-ending box-related code with `createLibContext()` and `destroyLibContext()`, one can use `FaustContext` like this:

```python
from dawdreamer.faust import FaustContext
from dawdreamer.faust.box import boxAdd, boxReal, boxWire

with FaustContext():
    # any box-related code can be used in the context.
    box = boxAdd(boxReal(0.5), boxWire())
```

The code above is equivalent to the following:
```python
createLibContext()
box = boxAdd(boxReal(0.5), boxWire())
destroyLibContext()
```

## Tools

Let's first import libraries and define helper functions.

In [3]:
if 'google.colab' in str(get_ipython()):
    !pip install numpy librosa scipy ipython

In [4]:
try:
    import dawdreamer
except ModuleNotFoundError:
    !pip install dawdreamer

In [9]:
import dawdreamer as daw
from dawdreamer.faust import createLibContext, destroyLibContext, FaustContext
from dawdreamer.faust.box import *

import numpy as np
import librosa
from scipy.io import wavfile
from IPython.display import Audio
import IPython.display as ipd

SAMPLE_RATE = 44100

def show_audio(data, autoplay=False):
    # Only normalize the audio if it's too loud
    if abs(data).max() > 1.:
        data /= abs(data).max()
    
    ipd.display(Audio(data=data, rate=SAMPLE_RATE, normalize=False, autoplay=autoplay))
    

engine = daw.RenderEngine(SAMPLE_RATE, 1)

playback_processor = engine.make_playback_processor("playback", np.zeros((2,1)))
faust_processor = engine.make_faust_processor("faust")

faust_processor.set_dsp_string("process = si.bus(2);")

engine.load_graph([
    (playback_processor, []),
    (faust_processor, ["playback"])
])

def render(duration=5, display=True):
    engine.render(duration)
    audio = engine.get_audio()
    if display:
        show_audio(audio)
    return audio

## Examples

For each example, the equivalent Faust DSP program and SVG diagram are given as helpers. The SVG diagram shows the result of the compilation *propagate* step (so before any of the signal normalization steps).

### Expression generating constant signals

Let's create a program generating a parallel construction of 7 and 3.14 constant values. Here is the Faust DSP code:

![exfaust0.svg](https://faustdoc.grame.fr/tutorials/box-api/exfaust0/exfaust0.svg)

```faust
process = 7,3.14;
```

[Try it Yourself >>](https://faustide.grame.fr/?code=https://faustdoc.grame.fr/tutorials/box-api/exfaust0/exfaust0.dsp)

The following code creates a box expression, containing a box `boxPar(boxInt(7), boxReal(3.14))` expression, then compiles it and displays the C++ class:

In [10]:
with FaustContext():
    
    box = boxPar(boxInt(7), boxReal(3.14))
    print(f'Box inputs: {box.inputs}, outputs: {box.outputs}')
    faust_processor.compile_box(box)

    print(render(display=False))
    print('C++ code:')
    print(boxToSource(box, 'cpp', 'MyDSP'))

Box inputs: 0, outputs: 2
[[7.   7.   7.   ... 7.   7.   7.  ]
 [3.14 3.14 3.14 ... 3.14 3.14 3.14]]
C++ code:
/* ------------------------------------------------------------
name: "dawdreamer"
Code generated with Faust 2.69.3 (https://faust.grame.fr)
Compilation options: -lang cpp -ct 1 -cn MyDSP -es 1 -mcd 16 -single -ftz 0
------------------------------------------------------------ */

#ifndef  __MyDSP_H__
#define  __MyDSP_H__

#ifndef FAUSTFLOAT
#define FAUSTFLOAT float
#endif 

#include <algorithm>
#include <cmath>
#include <cstdint>

#ifndef FAUSTCLASS 
#define FAUSTCLASS MyDSP
#endif

#ifdef __APPLE__ 
#define exp10f __exp10f
#define exp10 __exp10
#endif

#if defined(_WIN32)
#define RESTRICT __restrict
#else
#define RESTRICT __restrict__
#endif


class MyDSP : public dsp {
	
 private:
	
	int fSampleRate;
	
 public:
	MyDSP() {}

	void metadata(Meta* m) { 
		m->declare("compile_options", "-lang cpp -ct 1 -cn MyDSP -es 1 -mcd 16 -single -ftz 0");
		m->declare("name", "dawdreamer")

In the generated code above, look for the `compute` method. You'll find these lines:
```c++
output0[i1] = FAUSTFLOAT(7);
output1[i1] = FAUSTFLOAT(3.14f);
```
Remember that the Faust code was `process = 7,3.14;`, an infinite stream of 7 next to an infininte stream of 3.14.

## Basic operators

You may have wondered what `boxPar` meant earlier. It's the parallel operator in Faust, i.e., the `,` operator. Some other operators are outlined below.

| Box operator     | Faust expression | Resulting num inputs  | Resuluting num outputs | Requirements
|----------------- | ---------------- |----------------------|------------------ | ----------------|
| `boxPar(A, B)`   | `A, B`           | $$inputs(A)+inputs(B)$$ | $$outputs(A)+outputs(B)$$ | $$None$$
| `boxSeq(A, B)`   | `A : B`          | $$inputs(A)$$           | $$outputs(B)$$ | $$outputs(A)=inputs(B)$$
| `boxMerge(A, B)` | `A :> B`         | $$inputs(A)$$           | $$outputs(B)$$ | $$outputs(A)=k*inputs(B) \qquad \forall k>0$$
| `boxSplit(A, B)` | `A <: B`         | $$inputs(A)$$           | $$outputs(B)$$ | $$outputs(A)*k=inputs(B) \qquad \forall k>0$$
| `boxRec(A, B)`   | `A ~ B`          | $$inputs(A)-inputs(B)$$ | $$outputs(A)$$ | $$outputs(A) ≥ inputs(B) ≥ 1 $$ $$inputs(A) ≥ outputs(B) ≥ 1$$

For the next few blocks, we'll demonstrate many box operators which are also documented [here](https://dirt.design/DawDreamer/_generate/dawdreamer.faust.box.html) and tested [here](https://github.com/DBraun/DawDreamer/blob/feature/faust-signal-api/tests/test_libfaust_box.py).

## Doing some mathematical operations on an input signal

Here is a simple program doing a mathematical operation on an signal input:

![https://faustdoc.grame.fr/tutorials/box-api/exfaust1/exfaust1.svg](https://faustdoc.grame.fr/tutorials/box-api/exfaust1/exfaust1.svg)

```faust
process = _,3.14 : +;
```

[Try it Yourself >>](https://faustide.grame.fr/?code=https://faustdoc.grame.fr/tutorials/box-api/exfaust1/exfaust1.dsp)

In [11]:
with FaustContext():

    box = boxAdd(boxWire(), boxReal(3.14))

    faust_processor.compile_box(box)
    print(f"Num inputs: {faust_processor.get_num_input_channels()}, outputs: {faust_processor.get_num_output_channels()}")

    # Just one sample of a 1.0. The rest are read as zero.
    playback_processor.set_data(np.ones((faust_processor.get_num_input_channels(),1)))

    print(render(display=False))
    # the output should be 4.14 followed by 3.14 repeated


Num inputs: 1, outputs: 1
[[4.1400003 3.14      3.14      ... 3.14      3.14      3.14     ]]


## Sequencing boxes

Note that `boxAdd` is similar to many other box operators such as `boxDiv`, `boxSub`, `boxMul`, `boxAtan2`, and so on. These operators take two arguments where each argument is a box with exactly one output. You might be wondering how to add two boxes if they both have *two* outputs. In Faust, that code would be
```faust
process = _, _, _, _ :> _, _;
```

[Try it Yourself >>](https://faustide.grame.fr/?autorun=0&voices=8&name=untitled5&inline=cHJvY2VzcyA9IF8sIF8sIF8sIF8gOj4gXywgXzs%3D)

With boxes, we can use `boxMerge`:

```python
one = boxWire()
two = boxPar(one, one)
four = boxPar(two, two)
four2two = boxMerge(four, two)
```

We can even make a Python utility function for a [bus](https://faustlibraries.grame.fr/libs/signals/#sibus) of size N.

```python
from typing import List

def boxParN(boxes: List[Box]) -> Box:
    """Make a list of boxes parallel."""
    N = len(boxes)
    assert N > 0
    box = boxes.pop()
    while boxes:
        box = boxPar(boxes.pop(), box)

    return box

def bus(n: int) -> Box:
    # si.bus(n) in Faust
    if n == 0:
        raise ValueError("Can't make a bus of size zero.")
    else:
        return boxParN([boxWire() for _ in range(n)])
```
So our previous "add two stereo boxes" code would be:
```python
four2two = boxMerge(bus(4), bus(2))
```

Then suppose we had a box with 4 outputs. We could turn it into a new box with the same number of inputs but 2 outputs:
```python
boxWith4Outputs  # assume this came from somewhere
boxWith2Outputs = boxSeq(boxWith4Outputs, four2two)
```

## Defining a delay expression

Here is a simple program delaying the first input:

![exfaust2.svg](https://faustdoc.grame.fr/tutorials/box-api/exfaust2/exfaust2.svg)

```faust
process = @(_,7);
```

[Try it Yourself >>](https://faustide.grame.fr/?code=https://faustdoc.grame.fr/tutorials/box-api/exfaust2/exfaust2.dsp)

The prefix-notation `boxDelay(x, y)` operator is used to delay the `boxWire()` first parameter with the second `boxInt(7)`:

In [12]:
with FaustContext():

    box = boxDelay(boxWire(), boxInt(7))

    faust_processor.compile_box(box)
    print(f"Num inputs: {faust_processor.get_num_input_channels()}, outputs: {faust_processor.get_num_output_channels()}")

    # Our data is only one sample long, so all samples out of bounds are read as zero.
    data = np.ones((faust_processor.get_num_input_channels(),1))
    playback_processor.set_data(data)

    print(render(display=False)[0,:10])
    # The output should be our impulse delayed by 7 samples:
    # so [0. 0. 0. 0. 0. 0. 0. 1. 0. 0.]

Num inputs: 1, outputs: 1
[0. 0. 0. 0. 0. 0. 0. 1. 0. 0.]


Several options of the Faust compiler allow control of the generated C++ code. By default computation is done sample by sample in a single loop. But the compiler can also generate vector and parallel code. The following code show how to compile in vector mode:

In [13]:
with FaustContext():
    
    # Compile in vector mode: https://faustdoc.grame.fr/manual/compiler/#vector-code-generation
    # We can use these args in both the LLVM instrument (faust_processor) and the boxToSource function.
    argv = ["-vec", "-lv", "1"]

    box = boxDelay(boxWire(), boxInt(7))
    
    faust_processor.compile_box(box, argv)
    print(f"Num inputs: {faust_processor.get_num_input_channels()}, outputs: {faust_processor.get_num_output_channels()}")

    # Our data is only one sample long, so all samples out of bounds are read as zero.
    data = np.ones((faust_processor.get_num_input_channels(),1))
    playback_processor.set_data(data)

    print(render(display=False)[0,:10])
    print(boxToSource(box, 'cpp', 'MyDSP', argv))

Num inputs: 1, outputs: 1
[0. 0. 0. 0. 0. 0. 0. 1. 0. 0.]
/* ------------------------------------------------------------
name: "dawdreamer"
Code generated with Faust 2.69.3 (https://faust.grame.fr)
Compilation options: -lang cpp -ct 1 -cn MyDSP -es 1 -mcd 16 -single -ftz 0 -vec -lv 1 -vs 32
------------------------------------------------------------ */

#ifndef  __MyDSP_H__
#define  __MyDSP_H__

#ifndef FAUSTFLOAT
#define FAUSTFLOAT float
#endif 

#include <algorithm>
#include <cmath>
#include <cstdint>

#ifndef FAUSTCLASS 
#define FAUSTCLASS MyDSP
#endif

#ifdef __APPLE__ 
#define exp10f __exp10f
#define exp10 __exp10
#endif

#if defined(_WIN32)
#define RESTRICT __restrict
#else
#define RESTRICT __restrict__
#endif


class MyDSP : public dsp {
	
 private:
	
	float fYec1_perm[8];
	int fSampleRate;
	
 public:
	MyDSP() {}

	void metadata(Meta* m) { 
		m->declare("compile_options", "-lang cpp -ct 1 -cn MyDSP -es 1 -mcd 16 -single -ftz 0 -vec -lv 1 -vs 32");
		m->declare("name", "dawdrea

And can possibly be faster if the C++ compiler can auto-vectorize it.

If the delay operators are used on the input signal *before* the mathematical operations, then a *single delay* line will be created, taking the maximum size of both delay lines:

![exfaust3.svg](https://faustdoc.grame.fr/tutorials/box-api/exfaust3/exfaust3.svg)

```faust
process = _ <: @(500) + 0.5, @(3000) * 1.5;
```

[Try it Yourself >>](https://faustide.grame.fr/?code=https://faustdoc.grame.fr/tutorials/box-api/exfaust3/exfaust3.dsp)

And built with the following code:

In [14]:
with FaustContext():

    box = boxSplit(boxWire(), 
                   boxPar(boxAdd(boxDelay(boxWire(), 
                                          boxReal(500)), boxReal(0.5)),
                          boxMul(boxDelay(boxWire(), 
                                          boxReal(3000)), boxReal(1.5))))
    faust_processor.compile_box(box)
    print(f"Num inputs: {faust_processor.get_num_input_channels()}, outputs: {faust_processor.get_num_output_channels()}")
    print(boxToSource(box, 'cpp', 'MyDSP'))

Num inputs: 1, outputs: 2
/* ------------------------------------------------------------
name: "dawdreamer"
Code generated with Faust 2.69.3 (https://faust.grame.fr)
Compilation options: -lang cpp -ct 1 -cn MyDSP -es 1 -mcd 16 -single -ftz 0
------------------------------------------------------------ */

#ifndef  __MyDSP_H__
#define  __MyDSP_H__

#ifndef FAUSTFLOAT
#define FAUSTFLOAT float
#endif 

#include <algorithm>
#include <cmath>
#include <cstdint>

#ifndef FAUSTCLASS 
#define FAUSTCLASS MyDSP
#endif

#ifdef __APPLE__ 
#define exp10f __exp10f
#define exp10 __exp10
#endif

#if defined(_WIN32)
#define RESTRICT __restrict
#else
#define RESTRICT __restrict__
#endif


class MyDSP : public dsp {
	
 private:
	
	int IOTA1;
	float fVec1[4096];
	int fSampleRate;
	
 public:
	MyDSP() {}

	void metadata(Meta* m) { 
		m->declare("compile_options", "-lang cpp -ct 1 -cn MyDSP -es 1 -mcd 16 -single -ftz 0");
		m->declare("name", "dawdreamer");
	}

	virtual int getNumInputs() {
		return 1;
	}
	v

In the `void compute` method, the single fVec1 delay line is read at 2 differents indices.

## Equivalent box expressions

It is very important to note that *syntactically equivalent box expressions* will be *internally represented by the same memory structure* (using hash consing), thus treated in the same way in the further compilations steps. So the following code where the `s1` variable is created to define the `boxAdd(boxDelay(boxWire(), boxReal(500)), boxReal(0.5))` expression, then used in both outputs:

In [15]:
with FaustContext():

    b1 = boxAdd(boxDelay(boxWire(), boxReal(500)), boxReal(0.5))
    box = boxPar(b1, b1)

    print(f'Box inputs: {box.inputs}, outputs: {box.outputs}')
    faust_processor.compile_box(box)
    print(faust_processor.get_parameters_description())

Box inputs: 2, outputs: 2
[]


Will behave exactly the same as the following code, where the `boxAdd(boxDelay(boxWire(), boxReal(500)), boxReal(0.5))` expression is used twice:

In [16]:
with FaustContext():

    box = boxPar(boxAdd(boxDelay(boxWire(), boxReal(500)), boxReal(0.5)),
                 boxAdd(boxDelay(boxWire(), boxReal(500)), boxReal(0.5)))

    print(f'Box inputs: {box.inputs}, outputs: {box.outputs}')
    faust_processor.compile_box(box)
    print(faust_processor.get_parameters_description())

Box inputs: 2, outputs: 2
[]


## Using User Interface items

User Interface items can be used, as in the following example, with an `hslider`:

![exfaust4.svg](https://faustdoc.grame.fr/tutorials/box-api/exfaust4/exfaust4.svg)

```faust
process = _,hslider("Freq [midi:ctrl 7][style:knob]", 100, 100, 2000, 1) : *;
```

[Try it Yourself >>](https://faustide.grame.fr/?code=https://faustdoc.grame.fr/tutorials/box-api/exfaust4/exfaust4.dsp)

Built with the following code:

In [17]:
with FaustContext():
    
    box = boxMul(boxWire(), 
                 boxHSlider("Freq [midi:ctrl 7][style:knob]", 
                            boxReal(100), 
                            boxReal(100), 
                            boxReal(2000), 
                            boxReal(1)))

    print(f'Box inputs: {box.inputs}, outputs: {box.outputs}')
    faust_processor.compile_box(box)
    print(faust_processor.get_parameters_description())

Box inputs: 1, outputs: 1
[{'index': 0, 'name': '/dawdreamer/Freq', 'numSteps': 1901, 'isDiscrete': False, 'label': 'Freq', 'min': 100.0, 'max': 2000.0, 'step': 1.0, 'value': 100.0}]


With the box API, the layout can be defined using the [labels-as-pathnames](https://faustdoc.grame.fr/manual/syntax/#labels-as-pathnames) syntax, as in the following example:

![exfaust5.svg](https://faustdoc.grame.fr/tutorials/box-api/exfaust5/exfaust5.svg)

```faust
import("stdfaust.lib"); 
freq = vslider("h:Oscillator/freq", 440, 50, 1000, 0.1); 
gain = vslider("h:Oscillator/gain", 0, 0, 1, 0.01); 
process = freq*gain;
```

[Try it Yourself >>](https://faustide.grame.fr/?code=https://faustdoc.grame.fr/tutorials/box-api/exfaust5/exfaust5.dsp)

In [18]:
with FaustContext():

    box = boxMul(boxVSlider("h:Oscillator/freq",
                            440.,
                            50.,
                            1000.,
                            0.1),
                 boxVSlider("h:Oscillator/gain",
                            0.,
                            0.,
                            1.,
                            0.01))

    print(f'Box inputs: {box.inputs}, outputs: {box.outputs}')
    faust_processor.compile_box(box)
    print(faust_processor.get_parameters_description())
    print(f"Num inputs: {faust_processor.get_num_input_channels()}, outputs: {faust_processor.get_num_output_channels()}")

Box inputs: 0, outputs: 1
[{'index': 0, 'name': '/Oscillator/freq', 'numSteps': 9501, 'isDiscrete': False, 'label': 'freq', 'min': 50.0, 'max': 1000.0, 'step': 0.10000000149011612, 'value': 440.0}, {'index': 1, 'name': '/Oscillator/gain', 'numSteps': 101, 'isDiscrete': False, 'label': 'gain', 'min': 0.0, 'max': 1.0, 'step': 0.009999999776482582, 'value': 0.0}]
Num inputs: 0, outputs: 1


## Defining recursive signals

Recursive signals can be defined using the boxRec expression. A one sample delay is automatically created to produce a valid computation. Here is a simple example:

![exfaust6.svg](https://faustdoc.grame.fr/tutorials/box-api/exfaust6/exfaust6.svg)

```faust
process = + ~ _;
```

[Try it Yourself >>](https://faustide.grame.fr/?code=https://faustdoc.grame.fr/tutorials/box-api/exfaust6/exfaust6.dsp)

Let's analyze why this works. We can verbosely refactor `process = + ~ _;` into:
```faust
A = +; // 2 inputs / 1 output
B = _; // 1 input  / 1 output
process = A ~ B;
```
The recursive composition `A ~ B` works because it satisfies the two necessary properties:
* $outputs(A) ≥ inputs(B) ≥ 1$
* $inputs(A) ≥ outputs(B) ≥ 1$

The resulting box output will have ($inputs(A)-outputs(B)$) inputs and $outputs(A)$ outputs.

## Accessing the global context

In Faust, the underlying audio engine sample rate and buffer size is accessed using the foreign function and constant mechanism. The values can also be used in the box language with the following helper functions:
* `boxBufferSize()`
* `boxSampleRate()`

So the following DSP program:
```faust
import("stdfaust.lib"); 
process = ma.SR, ma.BS;
```

results in two output channels, the first being the constant sample rate, and the second being the buffer size we chose when creating the DawDreamer [FaustProcessor](https://dirt.design/DawDreamer/_generate/dawdreamer.FaustProcessor.html).

In [19]:
with FaustContext():

    box = boxPar(boxSampleRate(), boxBufferSize())

    print(f'Box inputs: {box.inputs}, outputs: {box.outputs}')
    faust_processor.compile_box(box)
    print(faust_processor.get_parameters_description())
    print(f"Num inputs: {faust_processor.get_num_input_channels()}, outputs: {faust_processor.get_num_output_channels()}")

    data = np.ones((faust_processor.get_num_input_channels(),1))
    playback_processor.set_data(data)

    print(render(display=False)[:,:3].tolist())

Box inputs: 0, outputs: 2
[]
Num inputs: 0, outputs: 2
[[44100.0, 44100.0, 44100.0], [1.0, 1.0, 1.0]]


## Creating waveforms

The following DSP program defining a waveform:

![exfaust10.svg](https://faustdoc.grame.fr/tutorials/box-api/exfaust10/exfaust10.svg)

```faust
process = waveform { 0, 100, 200, 300, 400 };
```

[Try it Yourself >>](https://faustide.grame.fr/?code=https://faustdoc.grame.fr/tutorials/box-api/exfaust10/exfaust10.dsp)

Can be written with the code, where the size of the waveform is the first output, and the waveform content itself is the second output created with `boxWaveform`, to follow the [waveform semantic](https://faustdoc.grame.fr/manual/syntax/#waveform-primitive):

In [20]:
with FaustContext():

    box = boxWaveform([0, 100, 200, 300, 400])

    print(f'Box inputs: {box.inputs}, outputs: {box.outputs}')
    faust_processor.compile_box(box)
    print(faust_processor.get_parameters_description())
    print(f"Num inputs: {faust_processor.get_num_input_channels()}, outputs: {faust_processor.get_num_output_channels()}")

    data = np.ones((faust_processor.get_num_input_channels(),1))
    playback_processor.set_data(data)

    print(render(display=False)[:,:8].tolist())

Box inputs: 0, outputs: 2
[]
Num inputs: 0, outputs: 2
[[5.0, 5.0, 5.0, 5.0, 5.0, 5.0, 5.0, 5.0], [0.0, 100.0, 200.0, 300.0, 400.0, 0.0, 100.0, 200.0]]


## Creating tables

Read only and read/write tables can be created. The *read-only table* signal is created with `boxReadOnlyTable` and takes:

* a size first argument
* a content second argument
* a read index third argument (between 0 and size-1)

and produces the indexed table content as its single output. The following simple DSP example:

![exfaust8.svg](https://faustdoc.grame.fr/tutorials/box-api/exfaust8/exfaust8.svg)

```faust
process = 10,1,int(_) : rdtable;
```

[Try it Yourself >>](https://faustide.grame.fr/?code=https://faustdoc.grame.fr/tutorials/box-api/exfaust8/exfaust8.dsp)

Can be written with the code:

In [21]:
with FaustContext():

    box = boxReadOnlyTable(boxInt(10), boxInt(1), boxIntCast(boxWire()))

    print(f'Box inputs: {box.inputs}, outputs: {box.outputs}')
    faust_processor.compile_box(box)
    print(faust_processor.get_parameters_description())
    print(f"Num inputs: {faust_processor.get_num_input_channels()}, outputs: {faust_processor.get_num_output_channels()}")

    data = np.ones((faust_processor.get_num_input_channels(),1))
    playback_processor.set_data(data)

    print(render(display=False)[:,:5].tolist())

Box inputs: 1, outputs: 1
[]
Num inputs: 1, outputs: 1
[[1.0, 1.0, 1.0, 1.0, 1.0]]


## Creating a table with a waveform

Let's load waveform {-1., 0., 1., 0.} into an `rdtable`. The resulting box will take a single input (an integer lookup index) and have one output.

In [22]:
 with FaustContext():
        
    waveform_content = boxWaveform([-1., 0., 1., 0.])

    rdtable = boxReadOnlyTable()
    assert rdtable.valid
    assert rdtable.inputs == 3
    assert rdtable.outputs == 1

    joined = boxPar(waveform_content, boxWire())
    assert joined.valid
    assert joined.inputs == 1
    assert joined.outputs == 3

    box = boxSeq(joined, rdtable)

    print(f'Box inputs: {box.inputs}, outputs: {box.outputs}')
    faust_processor.compile_box(box)
    print(faust_processor.get_parameters_description())
    print(f"Num inputs: {faust_processor.get_num_input_channels()}, outputs: {faust_processor.get_num_output_channels()}")

    # data serves as an index lookup into the waveform
    data = np.expand_dims(np.arange(1000) % 4, 0)
    playback_processor.set_data(data)

    print(render(display=False)[:,:10].tolist())

Box inputs: 1, outputs: 1
[]
Num inputs: 1, outputs: 1
[[-1.0, 0.0, 1.0, 0.0, -1.0, 0.0, 1.0, 0.0, -1.0, 0.0]]


## Creating a read/write table

The *read/write table* signal is created with `boxWriteReadTable` and takes:
* a size first argument (positive, integer constant)
* a content second argument
* a write index a third argument (between 0 and size-1)
* the input of the table as fourth argument
* a read index as fifth argument (between 0 and size-1)

and produces the indexed table content as its single output. The following DSP example:

![exfaust9.svg](https://faustdoc.grame.fr/tutorials/box-api/exfaust9/exfaust9.svg)

```faust
process = 10,1,int(_) : rdtable;
```

[Try it Yourself >>](https://faustide.grame.fr/?code=https://faustdoc.grame.fr/tutorials/box-api/exfaust9/exfaust9.dsp)

Can be written with the code:

In [23]:
with FaustContext():

    box = boxWriteReadTable(boxInt(10),
                            boxInt(1), 
                            boxIntCast(boxWire()), 
                            boxIntCast(boxWire()), 
                            boxIntCast(boxWire()))

    print(f'Box inputs: {box.inputs}, outputs: {box.outputs}')
    faust_processor.compile_box(box)
    print(faust_processor.get_parameters_description())
    print(f"Num inputs: {faust_processor.get_num_input_channels()}, outputs: {faust_processor.get_num_output_channels()}")

    data = np.ones((faust_processor.get_num_input_channels(),1))
    playback_processor.set_data(data)

    print(render(display=False)[:,:5].tolist())

Box inputs: 3, outputs: 1
[]
Num inputs: 3, outputs: 1
[[1.0, 0.0, 0.0, 0.0, 0.0]]


## Creating soundfiles

The [soundfile](https://faustdoc.grame.fr/manual/syntax/#soundfile-primitive) primitive allows access to a list of externally defined sound resources, described as the list of their filename, or complete paths. It takes:

* the sound number (as a integer between 0 and 255 as a [constant numerical expression](https://faustdoc.grame.fr/manual/syntax/#constant-numerical-expressions))
* the read index in the sound (which will access the last sample of the sound if the read index is greater than the sound length)

The generated block has:

* two fixed outputs: the first one is the currently accessed sound length in frames, the second one is the currently accessed sound nominal sample rate
* several more outputs for the sound channels themselves, as a [constant numerical expression](https://faustdoc.grame.fr/manual/syntax/#constant-numerical-expressions)

The soundfile block is created with `boxSoundfile`. Thus the following DSP code:

![exfaust11.svg](https://faustdoc.grame.fr/tutorials/box-api/exfaust11/exfaust11.svg)

```faust
process = 0,0 : soundfile("sound[url:{'tango.wav'}]", 1);
```

[Try it Yourself >>](https://faustide.grame.fr/?code=https://faustdoc.grame.fr/tutorials/box-api/exfaust11/exfaust11.dsp)

Will be created using the box API with:

In [25]:
with FaustContext():

    box = boxSoundfile("sound[url:{'tango.wav'}]", 
                       boxInt(1),
                       boxInt(0),
                       boxInt(0))
    assert box.valid
    print(f'Box inputs: {box.inputs}, outputs: {box.outputs}')

Box inputs: 0, outputs: 3


## Using the boxFromDSP function

Complete DSP programs can be compiled to boxes using the `boxFromDSP` function, which takes a DSP program as a string while returning the created box and the number of inputs/outputs:

In [26]:
with FaustContext():

    box = boxFromDSP("process = os.osc(440) * .1;")
    assert box.valid
    print(f"Box inputs: {box.inputs}, outputs: {box.outputs}")

    faust_processor.compile_box(box)
    print('description:', faust_processor.get_parameters_description())
    print(f"Num inputs: {faust_processor.get_num_input_channels()}, outputs: {faust_processor.get_num_output_channels()}")

    data = np.ones((faust_processor.get_num_input_channels(),1))
    playback_processor.set_data(data)

    render(display=True)

Box inputs: 0, outputs: 1
description: []
Num inputs: 0, outputs: 1


The resulting box expression can possibly be reused in a more complex construction, as in the following example, where a filter is created using the `boxFromDSP` function, then called with a slider to control its frequency, and the actual input:

In [28]:
with FaustContext():
    
    # Create the filter without parameter.
    # boxfilter has two inputs (cutoff frequency and signal input) and one output
    boxfilter = boxFromDSP("process = fi.lowpass(5);")

    # Create the filter parameters and connect
    cutoff = boxHSlider("cutoff", boxReal(300), boxReal(100), boxReal(2000), boxReal(0.01))
    cutoffAndInput = boxPar(cutoff, boxWire())

    # cutoffAndInput has two outputs, so we can sequentially connect it to boxfilter which needs 2 two inputs.
    filteredInput = boxSeq(cutoffAndInput, boxfilter)

    # the final box has one input and one output
    box = filteredInput
    assert box.valid
    print(f'Box inputs: {box.inputs}, outputs: {box.outputs}')
    faust_processor.compile_box(box)
    print(faust_processor.get_parameters_description())
    print(f"Num inputs: {faust_processor.get_num_input_channels()}, outputs: {faust_processor.get_num_output_channels()}")

    data = -1.+2.*np.random.random((faust_processor.get_num_input_channels(),int(SAMPLE_RATE*5.)))

    print('audio input (loud!):')
    show_audio(data)
    playback_processor.set_data(data)
    print('audio output:')
    render(display=True)

Box inputs: 1, outputs: 1
[{'index': 0, 'name': '/dawdreamer/cutoff', 'numSteps': 190001, 'isDiscrete': False, 'label': 'cutoff', 'min': 100.0, 'max': 2000.0, 'step': 0.009999999776482582, 'value': 300.0}]
Num inputs: 1, outputs: 1
audio input (loud!):


audio output:


## Defining more complex expressions: phasor and oscillator

More complex signal expressions can be defined, creating boxes using auxiliary definitions. So the following DSP program:

![exfaust12.svg](https://faustdoc.grame.fr/tutorials/box-api/exfaust12/exfaust12.svg)

```faust
import("stdfaust.lib");
process = phasor(440)
with {
     decimalpart(x) = x-int(x);
     phasor(f) = f/ma.SR : (+ : decimalpart) ~ _;
};
```

[Try it Yourself >>](https://faustide.grame.fr/?code=https://faustdoc.grame.fr/tutorials/box-api/exfaust12/exfaust12.dsp)

Can be built using the following helper functions:

In [29]:
def decimalPart() -> Box:
    return boxSub(boxWire(), boxIntCast(boxWire()))

def phasor(freq: Box) -> Box:
    return boxSeq(boxDiv(freq, boxSampleRate()), 
                  boxRec(boxSplit(boxAdd(), decimalPart()), boxWire()))

And the main function combining them:

In [30]:
with FaustContext():

    box = phasor(boxReal(440))

    assert box.valid
    print(f'Box inputs: {box.inputs}, outputs: {box.outputs}')
    faust_processor.compile_box(box)
    print(faust_processor.get_parameters_description())
    print(f"Num inputs: {faust_processor.get_num_input_channels()}, outputs: {faust_processor.get_num_output_channels()}")

    data = -1.+2.*np.random.random((faust_processor.get_num_input_channels(),int(SAMPLE_RATE*5.)))

    playback_processor.set_data(data)
    print('audio output:')
    render(display=True)

Box inputs: 0, outputs: 1
[]
Num inputs: 0, outputs: 1
audio output:


Now the following oscillator:
    
![exfaust13.svg](https://faustdoc.grame.fr/tutorials/box-api/exfaust13/exfaust13.svg)

```faust
import("stdfaust.lib");
process = osc(440), osc(440)
with {
    decimalPart(x) = x-int(x);
    phasor(f) = f/ma.SR : (+ : decimalPart) ~ _;
    osc(f) = sin(2 * ma.PI * phasor(f));
};
```

[Try it Yourself >>](https://faustide.grame.fr/?code=https://faustdoc.grame.fr/tutorials/box-api/exfaust13/exfaust13.dsp)

Can be built with:

In [31]:
def osc(freq: Box) -> Box:
    return boxSin(boxMul(boxMul(boxReal(2.0), boxReal(3.141592653)), phasor(freq)))

with FaustContext():

    box = boxPar(osc(boxReal(440)), osc(boxReal(440)))

    assert box.valid
    print(f'Box inputs: {box.inputs}, outputs: {box.outputs}')
    faust_processor.compile_box(box)
    print(faust_processor.get_parameters_description())
    print(f"Num inputs: {faust_processor.get_num_input_channels()}, outputs: {faust_processor.get_num_output_channels()}")

    data = -1.+2.*np.random.random((faust_processor.get_num_input_channels(),int(SAMPLE_RATE*5.)))

    playback_processor.set_data(data)
    print('audio output:')
    render(display=True)

    print(boxToSource(box, 'cpp', 'MyDSP'))

Box inputs: 0, outputs: 2
[]
Num inputs: 0, outputs: 2
audio output:


/* ------------------------------------------------------------
name: "dawdreamer"
Code generated with Faust 2.69.3 (https://faust.grame.fr)
Compilation options: -lang cpp -ct 1 -cn MyDSP -es 1 -mcd 16 -single -ftz 0
------------------------------------------------------------ */

#ifndef  __MyDSP_H__
#define  __MyDSP_H__

#ifndef FAUSTFLOAT
#define FAUSTFLOAT float
#endif 

#include <algorithm>
#include <cmath>
#include <cstdint>
#include <math.h>

#ifndef FAUSTCLASS 
#define FAUSTCLASS MyDSP
#endif

#ifdef __APPLE__ 
#define exp10f __exp10f
#define exp10 __exp10
#endif

#if defined(_WIN32)
#define RESTRICT __restrict
#else
#define RESTRICT __restrict__
#endif


class MyDSP : public dsp {
	
 private:
	
	int fSampleRate;
	float fConst1;
	float fRec1[2];
	
 public:
	MyDSP() {}

	void metadata(Meta* m) { 
		m->declare("compile_options", "-lang cpp -ct 1 -cn MyDSP -es 1 -mcd 16 -single -ftz 0");
		m->declare("name", "dawdreamer");
	}

	virtual int getNumInputs() {
		return 0;
	}
	virtual 

Which produces a compute method, where one can see that since the same oscillator signal is used on both outputs, it is actually computed once and copied twice.

## Polyphonic MIDI controllable simple synthesizer

Here is a MIDI controlable simple synthesizer, first with the DSP code:

![exfaust15.svg](https://faustdoc.grame.fr/tutorials/box-api/exfaust15/exfaust15.svg)

```faust
import("stdfaust.lib");
process = organ, organ
with {
    decimalPart(x) = x-int(x);
    phasor(f) = f/ma.SR : (+ : decimalPart) ~ _;
    osc(f) = sin(2 * ma.PI * phasor(f));
    freq = nentry("freq", 100, 100, 3000, 0.01);
    gain = button("gate") : en.adsr(0.02, 0.1, 0.8, 0.1) * .05;
    organ = gain * (osc(freq) + osc(2 * freq));
};
```

[Try it Yourself >>](https://faustide.grame.fr/?autorun=1&voices=0&name=brass&inline=aW1wb3J0KCJzdGRmYXVzdC5saWIiKTsKcHJvY2VzcyA9IG9yZ2FuLCBvcmdhbgp3aXRoIHsKICAgIGRlY2ltYWxQYXJ0KHgpID0geC1pbnQoeCk7CiAgICBwaGFzb3IoZikgPSBmL21hLlNSIDogKCsgOiBkZWNpbWFsUGFydCkgfiBfOwogICAgb3NjKGYpID0gc2luKDIgKiBtYS5QSSAqIHBoYXNvcihmKSk7CiAgICBmcmVxID0gbmVudHJ5KCJmcmVxIiwgMTAwLCAxMDAsIDMwMDAsIDAuMDEpOwogICAgZ2FpbiA9IGJ1dHRvbigiZ2F0ZSIpIDogZW4uYWRzcigwLjAyLCAwLjEsIDAuOCwgMC4xKSAqIC4wNTsKICAgIG9yZ2FuID0gZ2FpbiAqIChvc2MoZnJlcSkgKyBvc2MoMiAqIGZyZXEpKTsKfTs%3D)

In [32]:
def osc(freq: Box) -> Box:
    return boxSin(boxMul(boxMul(boxReal(2.0), boxReal(np.pi)), phasor(freq)))

with FaustContext():

    # Follow the freq/gate/gain convention, 
    # see: https://faustdoc.grame.fr/manual/midi/#standard-polyphony-parameters
    # We also demonstrate that boxHSlider can take floats for arguments instead fo boxReal
    freq = boxHSlider("freq", 100, 100, 3000, .01)

    gain = boxFromDSP('process = button("gate") : en.adsr(0.02, 0.1, 0.8, 0.1) * .05;')

    organ = boxMul(gain, boxAdd(osc(freq), 
                                osc(boxMul(freq, boxInt(2)))))
    # Stereo
    box = boxPar(organ, organ)

    print(f'Box inputs: {box.inputs}, outputs: {box.outputs}')
    faust_processor.num_voices = 10
    faust_processor.compile_box(box)

    # Note that because we're using polyphony, the frequency/gain/gate parameters are hidden from
    # get_parameters_description(). They're not automatable because the MIDI information fully controls them.
    print('parameters: ', faust_processor.get_parameters_description())
    print(f"Num inputs: {faust_processor.get_num_input_channels()}, outputs: {faust_processor.get_num_output_channels()}")

    data = -1.+2.*np.random.random((faust_processor.get_num_input_channels(),int(SAMPLE_RATE*5.)))

    playback_processor.set_data(data)

    faust_processor.clear_midi()
    # Add midi notes (pitch, velocity, start time, duration)
    faust_processor.add_midi_note(60, 127, 0.0, 0.6)
    faust_processor.add_midi_note(62, 127, 0.2, 0.4)
    faust_processor.add_midi_note(64, 127, 0.4, 0.2)
    faust_processor.add_midi_note(60, 127, 1.0, 0.8)
    faust_processor.add_midi_note(64, 127, 1.0, 0.8)
    faust_processor.add_midi_note(67, 127, 1.0, 0.8)
    faust_processor.add_midi_note(72, 64, 1.0, 0.8)

    print('audio output:')
    render(display=True)

    # to make this cell not affect the other cells in this notebook
    faust_processor.clear_midi()
    faust_processor.num_voices = 0


Box inputs: 0, outputs: 2
parameters:  []
Num inputs: 0, outputs: 2
audio output:


## Where to go from here?

Now that you've learned the basics of the box API, you can learn about converting boxes into Python JAX code. JAX code is differentiable, scalable, and fast!

[![Open in Colab](https://colab.research.google.com/assets/colab-badge.svg)](http://colab.research.google.com/github/DBraun/DawDreamer/blob/main/examples/Faust_to_JAX/Faust_to_JAX.ipynb)